# IMPORTS

In [9]:
import numpy as np  # useful for many scientific computing in Python
import pandas as pd # primary data structure library
!conda install -c anaconda xlrd --yes
!conda install -c conda-forge folium=0.5.0 --yes
import folium


import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

import itertools
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.ticker import NullFormatter
import pandas as pd
import numpy as np
import matplotlib.ticker as ticker
from sklearn import preprocessing
%matplotlib inline


import types
from botocore.client import Config
import ibm_boto3


!pip install bs4

Fetching package metadata .............
Solving package specifications: .

Package plan for installation in environment /opt/conda/envs/DSX-Python35:

The following packages will be SUPERSEDED by a higher-priority channel:

    xlrd: 1.1.0-py35h45a0a2a_1 --> 1.1.0-py35_1 anaconda

xlrd-1.1.0-py3 100% |################################| Time: 0:00:00  41.67 MB/s
Fetching package metadata .............
Solving package specifications: .

Package plan for installation in environment /opt/conda/envs/DSX-Python35:

The following NEW packages will be INSTALLED:

    altair:  2.2.2-py35_1 conda-forge
    branca:  0.3.1-py_0   conda-forge
    folium:  0.5.0-py_0   conda-forge
    vincent: 0.4.4-py_1   conda-forge

altair-2.2.2-p 100% |################################| Time: 0:00:00  54.19 MB/s
branca-0.3.1-p 100% |################################| Time: 0:00:00  35.38 MB/s
vincent-0.4.4- 100% |################################| Time: 0:00:00  40.38 MB/s
folium-0.5.0-p 100% |######################

In [10]:
# define the world map centered around Canada with a low zoom level
world_map = folium.Map(location=[41.39, 2.169], zoom_start=13)


# DATA PREPARATION 

In [11]:

def __iter__(self): return 0

# @hidden_cell
# The following code accesses a file in your IBM Cloud Object Storage. It includes your credentials.
# You might want to remove those credentials before you share your notebook.
client_123527ba066f49c695fd3f1f8e807ef8 = ibm_boto3.client(service_name='s3',
    ibm_api_key_id='cMW9WhbESXESXEU6uHPsl87yiYqA0xrfKcsiRsZAsbmM',
    ibm_auth_endpoint="https://iam.bluemix.net/oidc/token",
    config=Config(signature_version='oauth'),
    endpoint_url='https://s3-api.us-geo.objectstorage.service.networklayer.com')

body = client_123527ba066f49c695fd3f1f8e807ef8.get_object(Bucket='alquiler-donotdelete-pr-xp1hd7o49uunhu',Key='TRANSPORTS.csv')['Body']
# add missing __iter__ method, so pandas accepts body as file-like object
if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )

df_data_1 = pd.read_csv(body)
df_data_1.head()



CODI_CAPA                     CAPA_GENERICA                    NOM_CAPA  \
0      K001  Transports i serveis relacionats  Metro i línies urbanes FGC   
1      K001  Transports i serveis relacionats  Metro i línies urbanes FGC   
2      K001  Transports i serveis relacionats  Metro i línies urbanes FGC   
3      K001  Transports i serveis relacionats  Metro i línies urbanes FGC   
4      K001  Transports i serveis relacionats  Metro i línies urbanes FGC   

   ED50_COORD_X  ED50_COORD_Y  ETRS89_COORD_X  ETRS89_COORD_Y  LONGITUD  \
0    426477.889   4583649.008      426385.994     4583448.062  2.119370   
1    427818.595   4583478.761      427726.688     4583277.816  2.135427   
2    432051.444   4589400.176      431959.500     4589199.175  2.185391   
3    431149.447   4590452.022      431057.511     4590251.011  2.174473   
4    430579.417   4582275.812      430487.484     4582074.877  2.168588   

     LATITUD                                         EQUIPAMENT  DISTRICTE  \
0  41.399203  FGC (L6) - REINA ELISENDA (Sortida Duquesa d'O...        5.0   
1  41.397791                            FGC (L6) - LA BONANOVA-        5.0   
2  41.451492      METRO (L11) - CASA DE L'AIGUA (C. Vila-Real)-        8.0   
3  41.460889    METRO (L11) - CIUTAT MERIDIANA (C. Pedraforca)-        8.0   
4  41.387200         METRO (L1) - CATALUNYA (Rda. Universitat)-        2.0   

   BARRI        NOM_DISTRICTE               NOM_BARRI ADRECA TELEFON  
0   23.0  Sarrià-Sant Gervasi                  Sarrià    NaN     NaN  
1   26.0  Sarrià-Sant Gervasi  Sant Gervasi - Galvany    NaN     NaN  
2   53.0           Nou Barris        la Trinitat Nova    NaN     NaN  
3   55.0           Nou Barris        Ciutat Meridiana    NaN     NaN  
4    7.0             Eixample  la Dreta de l'Eixample    NaN     NaN

In [12]:
# instantiate a feature group for the TRANSPORT NETWROK IN BARCELONA
transport = folium.map.FeatureGroup()

# loop through the Public transportation to the  feature group
for lat, lng, in zip(df_data_1.LATITUD, df_data_1.LONGITUD):
    transport.add_child(
        folium.features.CircleMarker(
            [lat, lng],
            radius=2, # define how big you want the circle markers to be
            color='yellow',
            fill=True,
            fill_color='blue',
            fill_opacity=0.6
        )
    )

# add to map
world_map.add_child(transport)

In [13]:
#average rent price 2018 by neighborhood by m2

body = client_123527ba066f49c695fd3f1f8e807ef8.get_object(Bucket='alquiler-donotdelete-pr-xp1hd7o49uunhu',Key='historico-precios.csv')['Body']
# add missing __iter__ method, so pandas accepts body as file-like object
if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )

df_data_4 = pd.read_csv(body)
df_data_4.head()

del df_data_4["Unnamed: 2"]
df_data_4.head(14)


distrito  4q 2018
0          Ciutat Vella     18.9
1              Eixample     17.9
2                Gràcia     15.9
3        Horta-Guinardó     13.5
4             Les Corts     16.0
5            Nou Barris     14.0
6           Sant Andreu     12.9
7            Sant Martí     18.5
8        Sants-Montjuïc     15.8
9   Sarrià-Sant Gervasi     16.9
10             Badalona     17.3
11        Castelldefels     14.2

In [14]:
#barcelona Json

!wget --quiet https://cdn.rawgit.com/martgnz/bcn-geodata/master/barris/barris_geo.json -O world_countries.json
    
print('GeoJSON file downloaded!')

world_geo = r'world_countries.json' # geojson file


GeoJSON file downloaded!


In [15]:

# create a plain world map centered in BCN

world_map2 = folium.Map(location=[41.39, 2.169], zoom_start=13)


In [16]:
# generate choropleth map rent price
world_map2.choropleth(
    geo_data=world_geo,
    data=df_data_4,
    columns=['distrito', '4q 2018'],
    key_on='feature.properties.N_Distri',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='rent'
)

# adding  the transport netowork in the map
transport = folium.map.FeatureGroup()

# loop through the Public transportation to the  feature group
for lat, lng, in zip(df_data_1.LATITUD, df_data_1.LONGITUD):
    transport.add_child(
        folium.features.CircleMarker(
            [lat, lng],
            radius=2, # define how big you want the circle markers to be
            color='yellow',
            fill=True,
            fill_color='blue',
            fill_opacity=0.6
        )
    )

# add incidents to map
world_map2.add_child(transport)

world_map2

In [17]:
# neighborhood population by academic level
body = client_123527ba066f49c695fd3f1f8e807ef8.get_object(Bucket='alquiler-donotdelete-pr-xp1hd7o49uunhu',Key='2018_padro_nivell_academic (barrios).csv')['Body']
# add missing __iter__ method, so pandas accepts body as file-like object
if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )

df_data_6 = pd.read_csv(body)
df_data_6.head()



Nom_Districte  Sense estudis  \
0         Ciutat Vella           1939   
1             Eixample           3543   
2       Sants-Montjuïc           4519   
3            Les Corts           1101   
4  Sarrià-Sant Gervasi            823   

   Estudis primaris / certificat d'escolaritat / EGB  \
0                                              21106   
1                                              27244   
2                                              34143   
3                                               7634   
4                                               7281   

   Batxillerat elemental / graduat escolar / ESO / FPI  \
0                                              19544     
1                                              40077     
2                                              38078     
3                                              11295     
4                                              14906     

   Batxillerat superior / BUP / COU / FPII / CFGM grau mitjà  \
0                                              18210           
1                                              61794           
2                                              38305           
3                                              19274           
4                                              35630           

   Estudis universitaris / CFGS grau superior  No consta  
0                                       28636       1135  
1                                      100289       2835  
2                                       42068       2306  
3                                       30714       1044  
4                                       63104       2630

In [18]:
del df_data_6["No consta"]

In [19]:
results = df_data_6.sort_values("Nom_Districte").reset_index()
del results["index"]
results.head()


Nom_Districte  Sense estudis  \
0    Ciutat Vella           1939   
1        Eixample           3543   
2          Gràcia           1892   
3  Horta-Guinardó           5356   
4       Les Corts           1101   

   Estudis primaris / certificat d'escolaritat / EGB  \
0                                              21106   
1                                              27244   
2                                              12555   
3                                              28504   
4                                               7634   

   Batxillerat elemental / graduat escolar / ESO / FPI  \
0                                              19544     
1                                              40077     
2                                              18126     
3                                              37266     
4                                              11295     

   Batxillerat superior / BUP / COU / FPII / CFGM grau mitjà  \
0                                              18210           
1                                              61794           
2                                              27731           
3                                              37948           
4                                              19274           

   Estudis universitaris / CFGS grau superior  
0                                       28636  
1                                      100289  
2                                       44395  
3                                       36624  
4                                       30714

In [20]:
temp = df_data_1.groupby(['NOM_DISTRICTE']).count().reset_index()
temp.head()


NOM_DISTRICTE  CODI_CAPA  CAPA_GENERICA  NOM_CAPA  ED50_COORD_X  \
0    Ciutat Vella         27             27        27            27   
1        Eixample        120            120       120           120   
2          Gràcia         17             17        17            17   
3  Horta-Guinardó         31             31        31            31   
4       Les Corts         24             24        24            24   

   ED50_COORD_Y  ETRS89_COORD_X  ETRS89_COORD_Y  LONGITUD  LATITUD  \
0            27              27              27        27       27   
1           120             120             120       120      120   
2            17              17              17        17       17   
3            31              31              31        31       31   
4            24              24              24        24       24   

   EQUIPAMENT  DISTRICTE  BARRI  NOM_BARRI  ADRECA  TELEFON  
0          27         27     27         27       2        2  
1         120        120    120        120       0        0  
2          17         17     17         17       0        0  
3          31         31     31         31       0        0  
4          24         24     24         24       0        0

In [21]:
results["METRO"] = temp[["CAPA_GENERICA"]].astype(int)
results.head()

Nom_Districte  Sense estudis  \
0    Ciutat Vella           1939   
1        Eixample           3543   
2          Gràcia           1892   
3  Horta-Guinardó           5356   
4       Les Corts           1101   

   Estudis primaris / certificat d'escolaritat / EGB  \
0                                              21106   
1                                              27244   
2                                              12555   
3                                              28504   
4                                               7634   

   Batxillerat elemental / graduat escolar / ESO / FPI  \
0                                              19544     
1                                              40077     
2                                              18126     
3                                              37266     
4                                              11295     

   Batxillerat superior / BUP / COU / FPII / CFGM grau mitjà  \
0                                              18210           
1                                              61794           
2                                              27731           
3                                              37948           
4                                              19274           

   Estudis universitaris / CFGS grau superior  METRO  
0                                       28636     27  
1                                      100289    120  
2                                       44395     17  
3                                       36624     31  
4                                       30714     24

In [22]:
results["price_rent"] = df_data_4[["4q 2018"]]

results.head(15)


Nom_Districte  Sense estudis  \
0         Ciutat Vella           1939   
1             Eixample           3543   
2               Gràcia           1892   
3       Horta-Guinardó           5356   
4            Les Corts           1101   
5           Nou Barris           6953   
6          Sant Andreu           3545   
7           Sant Martí           6051   
8       Sants-Montjuïc           4519   
9  Sarrià-Sant Gervasi            823   

   Estudis primaris / certificat d'escolaritat / EGB  \
0                                              21106   
1                                              27244   
2                                              12555   
3                                              28504   
4                                               7634   
5                                              38976   
6                                              25967   
7                                              39647   
8                                              34143   
9                                               7281   

   Batxillerat elemental / graduat escolar / ESO / FPI  \
0                                              19544     
1                                              40077     
2                                              18126     
3                                              37266     
4                                              11295     
5                                              43266     
6                                              33602     
7                                              49846     
8                                              38078     
9                                              14906     

   Batxillerat superior / BUP / COU / FPII / CFGM grau mitjà  \
0                                              18210           
1                                              61794           
2                                              27731           
3                                              37948           
4                                              19274           
5                                              31975           
6                                              33164           
7                                              50085           
8                                              38305           
9                                              35630           

   Estudis universitaris / CFGS grau superior  METRO  price_rent  
0                                       28636     27        18.9  
1                                      100289    120        17.9  
2                                       44395     17        15.9  
3                                       36624     31        13.5  
4                                       30714     24        16.0  
5                                       20829     39        14.0  
6                                       29049     40        12.9  
7                                       54156     70        18.5  
8                                       42068     53        15.8  
9                                       63104     66        16.9

In [23]:
results.rename(columns={'Nom_Districte':'Neighborhood', 'Sense estudis':'No Studies', "Estudis primaris / certificat d'escolaritat / EGB":'Primary Education', 'Batxillerat elemental / graduat escolar / ESO / FPI':'Secondary Education', 'Batxillerat superior / BUP / COU / FPII / CFGM grau mitjà':'Higher Secondary Education', 'Estudis universitaris / CFGS grau superior':'University'}, inplace=True)


# DATAFRAMRE FINAL STEPS

In [24]:
results.head(15)

Neighborhood  No Studies  Primary Education  Secondary Education  \
0         Ciutat Vella        1939              21106                19544   
1             Eixample        3543              27244                40077   
2               Gràcia        1892              12555                18126   
3       Horta-Guinardó        5356              28504                37266   
4            Les Corts        1101               7634                11295   
5           Nou Barris        6953              38976                43266   
6          Sant Andreu        3545              25967                33602   
7           Sant Martí        6051              39647                49846   
8       Sants-Montjuïc        4519              34143                38078   
9  Sarrià-Sant Gervasi         823               7281                14906   

   Higher Secondary Education  University  METRO  price_rent  
0                       18210       28636     27        18.9  
1                       61794      100289    120        17.9  
2                       27731       44395     17        15.9  
3                       37948       36624     31        13.5  
4                       19274       30714     24        16.0  
5                       31975       20829     39        14.0  
6                       33164       29049     40        12.9  
7                       50085       54156     70        18.5  
8                       38305       42068     53        15.8  
9                       35630       63104     66        16.9

In [25]:
#average price m2 buy by neighboorhod: 2018 barcelona

body = client_123527ba066f49c695fd3f1f8e807ef8.get_object(Bucket='alquiler-donotdelete-pr-xp1hd7o49uunhu',Key='historico-precios-venta_trimestral_esp_201812.csv')['Body']
# add missing __iter__ method, so pandas accepts body as file-like object
if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )

df_data_7 = pd.read_csv(body)
df_data_7.head(15)
df_data_7.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10 entries, 0 to 9
Data columns (total 2 columns):
distrito    10 non-null object
4q 2018     10 non-null int64
dtypes: int64(1), object(1)
memory usage: 240.0+ bytes


In [26]:
results["price_buy"] = df_data_7[["4q 2018"]]
results.head(15)

Neighborhood  No Studies  Primary Education  Secondary Education  \
0         Ciutat Vella        1939              21106                19544   
1             Eixample        3543              27244                40077   
2               Gràcia        1892              12555                18126   
3       Horta-Guinardó        5356              28504                37266   
4            Les Corts        1101               7634                11295   
5           Nou Barris        6953              38976                43266   
6          Sant Andreu        3545              25967                33602   
7           Sant Martí        6051              39647                49846   
8       Sants-Montjuïc        4519              34143                38078   
9  Sarrià-Sant Gervasi         823               7281                14906   

   Higher Secondary Education  University  METRO  price_rent  price_buy  
0                       18210       28636     27        18.9       4434  
1                       61794      100289    120        17.9       5005  
2                       27731       44395     17        15.9       4346  
3                       37948       36624     31        13.5       3092  
4                       19274       30714     24        16.0       4896  
5                       31975       20829     39        14.0       2491  
6                       33164       29049     40        12.9       2926  
7                       50085       54156     70        18.5       4214  
8                       38305       42068     53        15.8       3621  
9                       35630       63104     66        16.9       5351

In [27]:
# import GPS Coordinates from city building for each neighborhood

body = client_123527ba066f49c695fd3f1f8e807ef8.get_object(Bucket='alquiler-donotdelete-pr-xp1hd7o49uunhu',Key='Posiciones.csv')['Body']
# add missing __iter__ method, so pandas accepts body as file-like object
if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )

barrios = pd.read_csv(body)
barrios.head()


distrito  Longitud    Latitud
0    Ciutat Vella  2.199700  41.384900
1        Eixample  2.163360  41.390254
2          Gràcia  2.160240  41.406970
3  Horta-Guinardó  2.136152  41.429920
4       Les Corts  2.129940  41.392540

In [28]:
results

results['lat'] = barrios['Latitud']
results['lng'] = barrios['Longitud']

# I can add marker one by one on the map
for i in range(0,len(barrios)):
    folium.Marker([barrios.iloc[i]['Latitud'], barrios.iloc[i]['Longitud']], popup=barrios.iloc[i]['distrito']).add_to(world_map2)


world_map2

---

# PLEASE INSERT HERE YOUR WORKING NEIGHBORHOOD and we will give recomendend the best neighborhoods to live based on rent price, commute distance.  

In [178]:
print ("Select where you will work? \n 0 Ciutat Vella \n 1 Eixample \n 2 Gràcia \n 3 Horta-Guinardó \n 4 Les Corts \n 5 Nou Barris \n 6 Sant Andreu \n 7 Sant Martí \n 8 Sants-Montjuïc \n 9 Sarrià-Sant Gervasi")
home= int(input("Please select from the list [0-9]: "))

#calculting the KM from the neighborhood to the rest of the neighborhoods
from math import sin, cos, sqrt, atan2, radians

distances = []
# approximate radius of earth in km
R = 6373.0

lat1 = radians(barrios.at[home, 'Latitud'])
lon1 = radians(barrios.at[home, 'Longitud'])

for lat, lng, in zip(barrios.Latitud, barrios.Longitud):
    dlon = radians(lng) - lon1
    dlat = radians(lat) - lat1
    a = sin(dlat / 2)**2 + cos(lat1) * cos(radians(lat)) * sin(dlon / 2)**2
    c = 2 * atan2(sqrt(a), sqrt(1 - a))
    result = R * c
    distances.append(result)
        
results["CommuteKM"] = distances

print("You have selected: ", barrios.at[home, 'distrito'])


print (distances)


Select where you will work? 
 0 Ciutat Vella 
 1 Eixample 
 2 Gràcia 
 3 Horta-Guinardó 
 4 Les Corts 
 5 Nou Barris 
 6 Sant Andreu 
 7 Sant Martí 
 8 Sants-Montjuïc 
 9 Sarrià-Sant Gervasi
Please select from the list [0-9]: 3
You have selected:  Horta-Guinardó
[7.2925772929481525, 4.961636557691547, 3.2485856566398326, 0.0, 4.189940273905572, 3.569659553699175, 5.20058455204887, 6.106017749057783, 7.7657993568757755, 2.3904594596425963]


In [179]:

results_clustering= results.drop(['No Studies','Primary Education','Secondary Education','Higher Secondary Education','University','Neighborhood'],1)
print(results_clustering.head())
results_clustering= preprocessing.StandardScaler().fit(results_clustering).transform(results_clustering)

kclusters = 4

results.reset_index()


# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(results_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

results['KMeans'] = kmeans.labels_


# create map
map_clusters = folium.Map(location=[41.39, 2.169], zoom_start=13)


    
    
map_clusters.choropleth(
    geo_data=world_geo,
    data=df_data_4,
    columns=['distrito', '4q 2018'],
    key_on='feature.properties.N_Distri',
    fill_color='PuRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='rent'
)

# adding  the transport netowork in the map
#transport = folium.map.FeatureGroup()

# loop through the Public transportation to the  feature group
#for lat, lng, in zip(df_data_1.LATITUD, df_data_1.LONGITUD):
#    transport.add_child(
#        folium.features.CircleMarker(
#            [lat, lng],
#            radius=2, # define how big you want the circle markers to be
#            color='yellow',
#            fill=False,
#           
#        )
#    )

    
    # set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(results['lat'], results['lng'], results['Neighborhood'], results['KMeans']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.9).add_to(map_clusters)
    
    
# add incidents to map
#map_clusters.add_child(transport)

folium.Marker([barrios.iloc[home]['Latitud'], barrios.iloc[home]['Longitud']], popup='YOUR WORK').add_to(map_clusters)

       
map_clusters


   METRO  price_rent  price_buy        lat       lng  CommuteKM  KMeans
0     27        18.9       4434  41.384900  2.199700   7.292577       3
1    120        17.9       5005  41.390254  2.163360   4.961637       2
2     17        15.9       4346  41.406970  2.160240   3.248586       1
3     31        13.5       3092  41.429920  2.136152   0.000000       0
4     24        16.0       4896  41.392540  2.129940   4.189940       1


In [180]:
resultmean= results.groupby('KMeans').mean()
resultmean.drop(['Primary Education','No Studies','Secondary Education','Higher Secondary Education','University','lat','lng'],1)

METRO  price_rent    price_buy  CommuteKM
KMeans                                               
0       36.666667   13.466667  2836.333333   2.923415
1       53.000000   15.800000  3621.000000   7.765799
2       72.333333   18.433333  4551.000000   6.120077
3       35.666667   16.266667  4864.333333   3.276328

In [105]:
results.corr()

No Studies  Primary Education  \
No Studies                    1.000000           0.946038   
Primary Education             0.946038           1.000000   
Secondary Education           0.927600           0.956136   
Higher Secondary Education    0.442481           0.491971   
University                   -0.145184          -0.060962   
METRO                         0.158337           0.274784   
price_rent                   -0.306562          -0.117813   
price_buy                    -0.744683          -0.659482   
lat                           0.287245           0.077726   
lng                           0.387596           0.539705   
CommuteKM                    -0.459183          -0.296291   
KMeans                        0.533505           0.646883   

                            Secondary Education  Higher Secondary Education  \
No Studies                             0.927600                    0.442481   
Primary Education                      0.956136                    0.491971   
Secondary Education                    1.000000                    0.700147   
Higher Secondary Education             0.700147                    1.000000   
University                             0.159546                    0.800592   
METRO                                  0.456920                    0.892345   
price_rent                            -0.125553                    0.181813   
price_buy                             -0.558490                    0.083739   
lat                                    0.156249                   -0.034750   
lng                                    0.450985                    0.062617   
CommuteKM                             -0.325967                   -0.017002   
KMeans                                 0.690872                    0.657214   

                            University     METRO  price_rent  price_buy  \
No Studies                   -0.145184  0.158337   -0.306562  -0.744683   
Primary Education            -0.060962  0.274784   -0.117813  -0.659482   
Secondary Education           0.159546  0.456920   -0.125553  -0.558490   
Higher Secondary Education    0.800592  0.892345    0.181813   0.083739   
University                    1.000000  0.888869    0.496719   0.615679   
METRO                         0.888869  1.000000    0.408851   0.359484   
price_rent                    0.496719  0.408851    1.000000   0.750768   
price_buy                     0.615679  0.359484    0.750768   1.000000   
lat                          -0.288707 -0.215022   -0.645951  -0.512028   
lng                          -0.186793  0.015606    0.170385  -0.353646   
CommuteKM                     0.281224  0.160200    0.491132   0.580079   
KMeans                        0.382730  0.604843   -0.128149  -0.341518   

                                 lat       lng  CommuteKM    KMeans  
No Studies                  0.287245  0.387596  -0.459183  0.533505  
Primary Education           0.077726  0.539705  -0.296291  0.646883  
Secondary Education         0.156249  0.450985  -0.325967  0.690872  
Higher Secondary Education -0.034750  0.062617  -0.017002  0.657214  
University                 -0.288707 -0.186793   0.281224  0.382730  
METRO                      -0.215022  0.015606   0.160200  0.604843  
price_rent                 -0.645951  0.170385   0.491132 -0.128149  
price_buy                  -0.512028 -0.353646   0.580079 -0.341518  
lat                         1.000000  0.174280  -0.885394 -0.151837  
lng                         0.174280  1.000000  -0.460385  0.172670  
CommuteKM                  -0.885394 -0.460385   1.000000  0.035067  
KMeans                     -0.151837  0.172670   0.035067  1.000000

In [106]:
results.describe()

No Studies  Primary Education  Secondary Education  \
count    10.000000          10.000000            10.000000   
mean   3572.200000       24305.700000         30600.600000   
std    2129.412219       11983.636659         13444.693767   
min     823.000000        7281.000000         11295.000000   
25%    1903.750000       14692.750000         18480.500000   
50%    3544.000000       26605.500000         35434.000000   
75%    5146.750000       32733.250000         39577.250000   
max    6953.000000       39647.000000         49846.000000   

       Higher Secondary Education    University       METRO  price_rent  \
count                   10.000000      10.00000   10.000000   10.000000   
mean                 35411.600000   44986.40000   48.700000   16.030000   
std                  13158.703087   23233.40694   30.594299    2.081159   
min                  18210.000000   20829.00000   17.000000   12.900000   
25%                  28792.000000   29465.25000   28.000000   14.450000   
50%                  34397.000000   39346.00000   39.500000   15.950000   
75%                  38215.750000   51715.75000   62.750000   17.650000   
max                  61794.000000  100289.00000  120.000000   18.900000   

         price_buy        lat        lng  CommuteKM     KMeans  
count    10.000000  10.000000  10.000000  10.000000  10.000000  
mean   4037.600000  41.405443   2.162890   4.290769   1.500000  
std     964.735681   0.024556   0.030435   2.415439   1.354006  
min    2491.000000  41.360290   2.119460   0.000000   0.000000  
25%    3224.250000  41.390825   2.137856   3.353602   0.250000  
50%    4280.000000  41.405799   2.161800   4.295523   1.500000  
75%    4780.500000  41.425553   2.192590   5.583240   2.000000  
max    5351.000000  41.439476   2.201122   8.621217   4.000000

In [107]:

import os
path = "CLOROPLETH_" + str(home) + '.html'
path

'CLOROPLETH_5.html'

In [108]:
map_clusters.save(path)